# Scaricare dati con CCXT

In [22]:
import ccxt
import pandas as pd
# from datetime import datetime, timedelta

def scarica_dati(exchange_name="bybit", symbol="BTC/USDT", timeframe="1m", start_date="2024-09-01", end_date="2024-10-01"):
    # Inizializza l'exchange
    exchange = getattr(ccxt, exchange_name)()
    
    # Converte le date in timestamp
    start_timestamp = exchange.parse8601(start_date + "T00:00:00Z")
    end_timestamp = exchange.parse8601(end_date + "T00:00:00Z")
    
    # Scarica i dati
    ohlcv = []
    while start_timestamp < end_timestamp:
        batch = exchange.fetch_ohlcv(symbol, timeframe, since=start_timestamp, limit=1000)
        if not batch:
            break
        ohlcv.extend(batch)
        start_timestamp = batch[-1][0] + 1
    
    # Crea un DataFrame
    df = pd.DataFrame(ohlcv, columns=['Timestamp', 'Open', 'High', 'Low', 'Close', 'Volume'])
    df['Timestamp'] = pd.to_datetime(df['Timestamp'], unit='ms')
    return df

In [23]:
# Scarica i dati
dati = scarica_dati(exchange_name="bybit", symbol="BTC/USDT", timeframe="1m", start_date="2024-10-01", end_date="2024-11-01")
dati

Timestamp      Open      High       Low     Close     Volume
0     2024-10-01 00:00:00  63309.05  63422.86  63308.65  63421.12  48.263832
1     2024-10-01 00:01:00  63421.12  63488.74  63384.91  63384.92  57.944510
2     2024-10-01 00:02:00  63384.92  63384.92  63305.08  63340.95  42.831644
3     2024-10-01 00:03:00  63340.95  63344.25  63267.30  63325.18  50.719298
4     2024-10-01 00:04:00  63325.18  63358.42  63323.60  63323.92  38.598535
...                   ...       ...       ...       ...       ...        ...
44951 2024-11-01 05:11:00  69534.48  69539.48  69525.51  69527.94   3.998571
44952 2024-11-01 05:12:00  69527.94  69566.40  69527.27  69549.27   5.113837
44953 2024-11-01 05:13:00  69549.27  69569.43  69546.27  69562.73   4.345560
44954 2024-11-01 05:14:00  69562.73  69570.57  69555.19  69555.19   0.953530
44955 2024-11-01 05:15:00  69555.19  69558.11  69525.19  69525.19  14.626591

[44956 rows x 6 columns]

# Identificazione dei pattern ricorrenti con ottimizzazione

In [24]:
import numpy as np
import hdbscan
from sklearn.preprocessing import StandardScaler
from collections import Counter
# import matplotlib.pyplot as plt

def calcola_variabili(dati):
    dati['Perc_Change_Open_Close'] = (dati['Close'] - dati['Open']) / dati['Open']
    dati['Perc_Change_High_Low'] = (dati['High'] - dati['Low']) / dati['Low']
    dati['Range_High_Low'] = dati['High'] - dati['Low']
    dati['Volatility'] = (dati['High'] - dati['Low']) / dati['Open']
    return dati

def crea_pattern_temporali(dati, finestra=5):
    patterns = []
    for i in range(len(dati) - finestra + 1):
        pattern = dati.iloc[i:i + finestra][['Perc_Change_Open_Close', 'Perc_Change_High_Low', 'Volatility']].values.flatten()
        patterns.append(pattern)
    return np.array(patterns)

def trova_pattern_hdbscan(dati, finestra=5, min_cluster_size=5):
    dati = calcola_variabili(dati)
    patterns = crea_pattern_temporali(dati, finestra)
    
    scaler = StandardScaler()
    patterns_scaled = scaler.fit_transform(patterns)
    
    clusterer = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size)
    clusters = clusterer.fit_predict(patterns_scaled)
    
    pattern_counts = Counter(clusters)
    pattern_counts = {k: v for k, v in sorted(pattern_counts.items(), key=lambda item: item[1], reverse=True)}
    
    classifica = pd.DataFrame({
        'Cluster': list(pattern_counts.keys()),
        'Frequenza': list(pattern_counts.values())
    })
    return classifica, clusters

def ottimizza_pattern_hdbscan(dati, finestre=[3, 5, 10], min_cluster_sizes=[3, 5, 10]):
    risultati = []
    for finestra in finestre:
        for min_cluster_size in min_cluster_sizes:
            _, clusters = trova_pattern_hdbscan(dati, finestra=finestra, min_cluster_size=min_cluster_size)
            num_cluster = len(set(clusters)) - (1 if -1 in clusters else 0)  # Escludi outlier
            risultati.append({
                "finestra": finestra,
                "min_cluster_size": min_cluster_size,
                "num_cluster": num_cluster
            })
    risultati_df = pd.DataFrame(risultati)
    migliori_parametri = risultati_df.sort_values(by="num_cluster", ascending=False).iloc[0]
    return migliori_parametri

In [25]:
# Ottimizza i parametri di HDBSCAN
parametri_pattern = ottimizza_pattern_hdbscan(dati)
print("Parametri ottimizzati per HDBSCAN:\n", parametri_pattern)

Parametri ottimizzati per HDBSCAN:
 finestra             3
min_cluster_size     5
num_cluster         12
Name: 1, dtype: int64


# Previsione dei prezzi futuri con random forest e ottimizzazione

In [ ]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import train_test_split

def suddividi_dati(dati, test_size=0.2, validation_size=0.2):
    train_val_data, test_data = train_test_split(dati, test_size=test_size, shuffle=False)
    train_data, val_data = train_test_split(train_val_data, test_size=validation_size / (1 - test_size), shuffle=False)
    return train_data, val_data, test_data

def mean_absolute_percentage_error(y_true, y_pred):
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def ottimizza_random_forest(dati, finestra, param_grid=None):
    if param_grid is None:
        param_grid = {
            'n_estimators': [50, 100, 200],
            'max_depth': [3, 5, 10],
            'min_samples_split': [2, 5],
            'min_samples_leaf': [1, 2, 4]
        }
    
    print("[INFO] Calcolo delle variabili derivate...")
    dati = calcola_variabili(dati)
    
    print(f"[INFO] Generazione dei pattern con finestra = {finestra}...")
    patterns = crea_pattern_temporali(dati, finestra)
    target = dati['Close'].iloc[finestra:].values  # Prezzi futuri di chiusura
    
    # Assicurati che le dimensioni siano coerenti
    patterns = patterns[:len(target)]
    print(f"[INFO] Pattern generati: {len(patterns)} campioni.")
    
    print("[INFO] Suddivisione dei dati in train, validation e test...")
    train_data, val_data, test_data = suddividi_dati(patterns, test_size=0.2, validation_size=0.2)
    train_target, val_target, test_target = suddividi_dati(target, test_size=0.2, validation_size=0.2)
    print(f"[INFO] Dimensioni dei dataset:")
    print(f"  Train: {len(train_data)} campioni")
    print(f"  Validation: {len(val_data)} campioni")
    print(f"  Test: {len(test_data)} campioni")
    
    print("[INFO] Inizio dell'ottimizzazione dei parametri della Random Forest con GridSearchCV...")
    rf = RandomForestRegressor(random_state=42)
    grid_search = GridSearchCV(rf, param_grid, cv=3, scoring='neg_mean_absolute_error', n_jobs=-1, verbose=10)
    grid_search.fit(train_data, train_target)
    
    print("[INFO] GridSearchCV completato.")
    print(f"[INFO] Migliori parametri trovati: {grid_search.best_params_}")
    best_model = grid_search.best_estimator_
    
    print("[INFO] Valutazione del modello sui dati di validation...")
    val_predictions = best_model.predict(val_data)
    errore_validation = mean_absolute_percentage_error(val_target, val_predictions)
    print(f"[INFO] Errore di validation (MAPE): {errore_validation:.4f}%")
    
    print("[INFO] Valutazione del modello sui dati di test...")
    test_predictions = best_model.predict(test_data)
    errore_test = mean_absolute_percentage_error(test_target, test_predictions)
    print(f"[INFO] Errore di test (MAPE): {errore_test:.4f}%")
    
    print("[INFO] Ottimizzazione completata.")
    return best_model, errore_validation, errore_test, grid_search.best_params_

In [ ]:
parametri_rf = {
    'n_estimators': [50, 100, 200],
    'max_depth': [3, 5, 10],
    'min_samples_split': [2, 5],
    'min_samples_leaf': [1, 2, 4]
}

# Ottimizzazione e valutazione
modello_rf, errore_val, errore_test, migliori_parametri_rf = ottimizza_random_forest(dati, parametri_pattern["finestra"], param_grid=parametri_rf)
print("Parametri ottimizzati per Random Forest:", migliori_parametri_rf)
print("MAPE validation:", errore_val)
print("MAPE test:", errore_test)

[INFO] Calcolo delle variabili derivate...
[INFO] Generazione dei pattern con finestra = 3...
[INFO] Pattern generati: 44953 campioni.
[INFO] Suddivisione dei dati in train, validation e test...
[INFO] Dimensioni dei dataset:
  Train: 26971 campioni
  Validation: 8991 campioni
  Test: 8991 campioni
[INFO] Inizio dell'ottimizzazione dei parametri della Random Forest con GridSearchCV...
Fitting 3 folds for each of 54 candidates, totalling 162 fits
[INFO] GridSearchCV completato.
[INFO] Migliori parametri trovati: {'max_depth': 3, 'min_samples_leaf': 1, 'min_samples_split': 2, 'n_estimators': 50}
[INFO] Valutazione del modello sui dati di validation...
[INFO] Errore di validation (MAPE): 6.0510%
[INFO] Valutazione del modello sui dati di test...
[INFO] Errore di test (MAPE): 8.7997%
[INFO] Ottimizzazione completata.
Parametri ottimizzati per Random Forest: {'max_depth': 3, 'min_samples_leaf': 1, 'min_samples_split': 2, 'n_estimators': 50}
Errore di validation: 6.051047508786162
Errore di 

# Previsione sui nuovi dati

In [28]:
import plotly.graph_objects as go
from datetime import datetime, timedelta

def prevedi_prezzi(modello, nuovi_dati, finestra=5):
    nuovi_dati = calcola_variabili(nuovi_dati)
    nuovi_pattern = crea_pattern_temporali(nuovi_dati, finestra)
    previsioni = modello.predict(nuovi_pattern)
    return previsioni

def pipeline_finale(dati, finestra=5):
    # 1. Ottieni la data corrente
    oggi = datetime.now()
    start_date = (oggi - timedelta(days=30)).strftime('%Y-%m-%d')
    end_date = oggi.strftime('%Y-%m-%d')
    
    print(f"[INFO] Scaricamento dati recenti da {start_date} a {end_date}...")
    dati_recenti = scarica_dati(start_date=start_date, end_date=end_date)
    print("[INFO] Dati recenti scaricati.")
    
    # 2. Ottimizza i pattern HDBSCAN
    parametri_pattern = ottimizza_pattern_hdbscan(dati)
    print("Parametri pattern:", parametri_pattern)
    
    # 3. Ottimizza la Random Forest
    modello_rf, errore_val, errore_test, migliori_parametri_rf = ottimizza_random_forest(dati, parametri_pattern["finestra"])
    print("Parametri Random Forest:", migliori_parametri_rf)
    print(f"Errore di validation (MAPE): {errore_val:.2f}%")
    print(f"Errore di test (MAPE): {errore_test:.2f}%")
    
    # 4. Prevedi sui nuovi dati
    print("[INFO] Generazione delle previsioni future...")
    previsioni = prevedi_prezzi(modello_rf, nuovi_dati=dati_recenti, finestra=parametri_pattern["finestra"])
    print(f"[INFO] Numero di dati forniti: {len(dati_recenti)}")
    print(f"[INFO] Numero di previsioni future: {len(previsioni)}")
    
    # 5. Grafico interattivo
    print("[INFO] Creazione del grafico interattivo...")
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        x=dati_recenti['Timestamp'], 
        y=dati_recenti['Close'], 
        mode='lines', 
        name='Dati Recenti', 
        line=dict(color='blue')
    ))
    
    # Crea un array di timestamp per le previsioni future
    last_timestamp = dati_recenti['Timestamp'].iloc[-1]
    future_timestamps = [last_timestamp + timedelta(minutes=i+1) for i in range(len(previsioni))]
    
    fig.add_trace(go.Scatter(
        x=future_timestamps, 
        y=previsioni, 
        mode='lines', 
        name='Previsioni Future', 
        line=dict(color='red')
    ))
    
    fig.update_layout(
        title="Dati Recenti e Previsioni Future",
        xaxis_title="Timestamp",
        yaxis_title="Prezzo",
        legend=dict(x=0, y=1, traceorder="normal"),
    )
    fig.show()
    
    return previsioni

In [29]:
# Esecuzione finale
previsioni_finali = pipeline_finale(dati, finestra=5)
print("Previsioni finali sui dati nuovi:", previsioni_finali)

[INFO] Scaricamento dati recenti da 2024-11-11 a 2024-12-11...
[INFO] Dati recenti scaricati.
Parametri pattern: finestra             3
min_cluster_size     5
num_cluster         12
Name: 1, dtype: int64
[INFO] Calcolo delle variabili derivate...
[INFO] Generazione dei pattern con finestra = 3...
[INFO] Pattern generati: 44953 campioni.
[INFO] Suddivisione dei dati in train, validation e test...
[INFO] Dimensioni dei dataset:
  Train: 26971 campioni
  Validation: 8991 campioni
  Test: 8991 campioni
[INFO] Inizio dell'ottimizzazione dei parametri della Random Forest con GridSearchCV...
Fitting 3 folds for each of 54 candidates, totalling 162 fits
[INFO] GridSearchCV completato.
[INFO] Migliori parametri trovati: {'max_depth': 3, 'min_samples_leaf': 1, 'min_samples_split': 2, 'n_estimators': 50}
[INFO] Valutazione del modello sui dati di validation...
[INFO] Errore di validation (MAPE): 6.0510%
[INFO] Valutazione del modello sui dati di test...
[INFO] Errore di test (MAPE): 8.7997%
[INFO

Previsioni finali sui dati nuovi: [63112.01301757 63202.38647902 63393.54859923 ... 63570.95212382
 63568.04438619 63577.10536727]


In [30]:
len(previsioni_finali)

43765